## 1. Hashing task!

* We've put all passwords from passwords1.txt and passwords2.txt  in two lists: listPasswords1 and listPasswords2

In [1]:
listPasswords1=[]
listPasswords2=[]
filePassword1 = open("passwords1.txt", 'r')
lines_p1 = filePassword1.readlines()
for line in lines_p1:
    listPasswords1.append(line.strip())

filePassword2 = open("passwords2.txt", 'r')
lines_p2 = filePassword2.readlines()
for line in lines_p2:
    listPasswords2.append(line.strip())



We have set all variables that we need to build our Bloom Filter:
* n = Number of items in the filter
* p = Probability of false positives, fraction between 0 and 1
* m = Number of bits in the filter (size of Bloom Filter bit-array)
* k = Number of hash functions

We did these following considerations:
N is the amount of passwords that are in passwordss1.txt (i.e. in listPasswords1).
We need to calculate p,m and k from following formulas:
\begin{align*}
k = (m/n)*ln(2)
\end{align*}

\begin{align*}
m = ((n*ln(p)) / (ln(2))^2
\end{align*}

Since we don't know the value of any previous varaibles, from https://hackernoon.com/probabilistic-data-structures-bloom-filter-5374112a7832 (suggested link in track) we have set initially p=0.0015. P must be a valuue between 0 and 1. With smaller value of p, we have a lower probability to have a false positives in search on bloom filter. 
Bloom filter can have false positives and NOT false negatives. We have choosen this value (0.0015) from a different test that we have tryed. We think that it should be an optimal value to have also optimal values about k and m.
Funally we calculated k and m (with previous formulas).

In [2]:
n=len(listPasswords1)
p=0.01
import math
m=math.ceil((n * math.log(p)) / math.log(1 / pow(2, math.log(2))))
k = round((m / n) * math.log(2))

This following function is our hash function. We have written from scratch our fnv function based on fnv hash function. FNV hashes are designed to be fast while maintaining a low collision rate. The FNV speed allows one to quickly hash lots of data while maintaining a reasonable collision rate. 
To build bloom filter we need of various hash functions that should be independent, uniformly distributed and fast.
From previous formulas, we have calculated the number of different hash functions that we should use. We set a variable, called 'seed' that is an integer from 0 to k(number of hash functions); in this way we'll have k different hash fucntions that transform our input string in k different number. These k numbers will be the index of our bit-array that represent respective inout password.

The initial values of 'FNV_prime' and 'offset_basis' are taken from this wikipedia page: https://en.wikipedia.org/wiki/Fowler–Noll–Vo_hash_function in 'FNV hash parameters'.


In [3]:
def fnv1_64(password, seed=0):
    """
    Returns: The FNV-1 hash of a given string. 
    """
    #Constants
    FNV_prime = 1099511628211
    offset_basis = 14695981039346656037

    #FNV-1a Hash Function
    hash = offset_basis + seed
    for char in password:
        hash = hash * FNV_prime
        hash = hash ^ ord(char)
    return hash




This following class 'BloomFilter' represent out Bloom Filter. 

It has three attributes:
* sizeArray = dimension of bit-array
* number_HashFucntion = number of hash functions
* array_BloomFilter = bit-array of bloom filter

It has also two methods:
* init: it takes, as parameteers ouur bloom filter, k (number of hash functions that we have calculated from previous formula), m  (size of bit-array that we have calculated with  previous function). It initializes the bit-array of Bloom filter (size=m) with all '0'; its size with m and its number of hash functions with k.
* add: this method allow to add an element from input list to our bloom filter. It takes this list and our bloom filter as parameters and it calculates the effective bit-array with right '1' and '0'.

In [4]:
class BloomFilter:

    sizeArray=0
    number_HashFucntion=0
    array_BloomFilter=[]
    
    @property
    def size(self):
        return self.sizeArray
    @property
    def numHash(self):
        return self.number_HashFucntion
    @property
    def arrayBloom(self):
        return self.array_BloomFilter
    
    def init(self,k,m):
        self.sizeArray=m
        self.number_HashFucntion=k
        
        for i in range(m):
            self.array_BloomFilter.append(0)
    
    def add(self,strings):
        #print(self.number_HashFucntion)
        #print(self.sizeArray)
        h=0
        for psw in strings:
            
            for seed in range(self.number_HashFucntion):
                index=fnv1_64(psw,seed) % self.sizeArray
                
                self.array_BloomFilter[index]=1

Then we made a function 'checkPassw' that checks how many password in listPasswords2 (i.e. in passowrds2.txt) are in our Bloom Filter. It takes our bloom filter and the list of passwords that are in passwords2.txt and it returns how many passwords are in bloom filter. 
A password is in our bloom filter if and only if its conversion with hash functions coresponds to every '1' in the bit-array. If there is only one '0', current password is not in bloom filter.

'countCheck' is the number of occurences of passwords (from passwords2.txt) in bloom filter. This number represent the occurences of passwords from passwords2.txt that are 'probably' in password1.txt

In [5]:
def checkPassw(BloomFilter, listPasswords2):
    countCheck=0
    for psw in listPasswords2:
        count=0
        for seed in range(BloomFilter.number_HashFucntion):
            index=fnv1_64(psw,seed) % BloomFilter.sizeArray
            if BloomFilter.array_BloomFilter[index]==1:
                count+=1
            if count==BloomFilter.number_HashFucntion:
                countCheck+=1
            
    return countCheck

## Bonus section: 
###### We calculate the number of false positive

This following function 'falsePositives' allows to calculate the exact number of false positive. It takes these following data, as parameter:
* Bloom Filter = our bloom filter
* listPassowrds1 = passwords from passwords1.txt
* listPassowrds2 = passwords from passwords2.txt

For every password in listPasswords2, it checks for every password, if current password is in the bloom filter. Then if this password is in bloom filter, it means that it is 'probably' in listPasswords2. To check if it's a false positive (i.e. it is not in listPAsswords1), we'll continue to verify if this current password is in listPassword1. If it's true, it means tht it is a False psiitive and we increment our counter 'countFalsePositives'; if it's True it means this password is actually in listPassword1 nad we continue with next password in listPassword2.

In [6]:
def falsePositives(BloomFilter, listPasswords1, listPasswords2):
    s= set(listPasswords1)
    countFalsePositives=0
    
    for psw in listPasswords2:
        count=0
        for seed in range(BloomFilter.number_HashFucntion):
            index=fnv1_64(psw,seed) % BloomFilter.sizeArray
            if (BloomFilter.array_BloomFilter[index]==1):
                    count+=1
            else:
                break
            if count==BloomFilter.number_HashFucntion:
                if not(psw in s):
                    countFalsePositives+=1
                    print(psw)
    return countFalsePositives
                

Then we did the main function, as wirtten in homework track. With this function we did these following steps:
* init bit-array, its size adn number of hash functions of our bloom filter, with 'BloomFilter.init(BloomFilter,k,m)'
* add passowrds from listPasswords1 into our bloom filter, with 'BloomFilter.add(BloomFilter,listPasswords1)'
* calculate how many passwords (from passwords2.txt) are present in our bloom filter, with 'checkPassw(BloomFilter,listPasswords2)'

###### Finally we print these following functions:
* Number of hash function used
* Number of duplicates detected
* Probability of false positives
* Execution time

In [7]:
import time

def BloomFilterFunc(listPasswords1, listPasswords2):
    start = time.time()
    #init our bloom filter
    BloomFilter.init(BloomFilter,k,m)
    #add all passowrd from listPassowrds1 to our bloom filter
    BloomFilter.add(BloomFilter,listPasswords1)
    #check and save into 'countPassw' the number of occurences of password (from passwords2) in the bloom filter
    countPassw=checkPassw(BloomFilter,listPasswords2)
    end = time.time()
    
    #print output data
    
    
    print('Number of hash function used: ', k)
    print('Number of duplicates detected: ', countPassw)
    print('Probability of false positives: ', p)
    print('Execution time: ', end-start)
    



* Execute main function

In [8]:
BloomFilterFunc(listPasswords1, listPasswords2)

Number of hash function used:  7
Number of duplicates detected:  14251447
Probability of false positives:  0.01
Execution time:  4041.6586632728577


* Execute bonus section

In [9]:
falsPositive=falsePositives(BloomFilter,listPasswords1,listPasswords2)

2Hx+:gK&v9RDN(Czebdu
rmH!5zN'PepJ<oX/7:y(
.cT7qK;U,Rx9#8Dl3)hj
S-=mt)2IwUf(Q4JN<@?A
jsQ/?-D.$y+(mPX)xIMR
(#<zxR@3-&rE>Jv"M'g5
InmKejMETSC$GZ?5,Jc%
-#.ipxQ!k=>TDY*As+mF
0=DxhvBUaKGPQb<tMfZH
hnjITO;0W@RPa-e5x87D
ATG+@8YoSxW*f)IZz"r5
U5Les,!8I"THYvNw:XO.
Qj?O4,YmAhPsnCRUve3S
'Kyk/LmUC"XOJ6BYAi*z
B8CAXIlQe7PY'vpanKqh
y/,+vP(reYWB:VTI9sZf
,Pr@NjuldqaSG'kR!=Ec
m&k.yh!1+c7O6(Hqia,9
aVTRuHB3/@W?qmNPF#6J
6f=BuvY#C9(-XhmWH,yU
53ewq?aTdluNv%EO-@FH
B)<&Hx5O+VRoDYrX>%6P
+MD5:2gw*=GHsN6-C!ui
=H/L<I:V4@15oEKqU%wi
Z/y40+pcLXbUxIRFl$7t
#;@c905Pubx1fpOk7>U:
uPM+p8gVO!D/HJLy:kif
&QYDRgTM)9zNXyskUC*E
$Op0PH-t8LlAozn"EdG6
j1RlY9NEWX(.a4deCIh)
UHpJ&yti8d1saTu/IxLW
l%Tz13gfJ9XY6AhaLicS
PR=iM!BHp@)y-.u<zwWh
'4z(OkSUpqMW+Q!DhC"?
S)v9DXFw!Kf;<WOPB%j0
+6;h-3apn<o'$QSgZEr1
&HCkTZD;S"q3xMhBi.fI
/$S-B#vYQZyh5OenJL8;
YjbdS"986=u#?13E4$.L
3$k).%ahquz9p#K'rj!6
qaPV*hg")&?N<z:XB,+3
>z9OleGsg8,2PbN'-DCQ
>UHWsVp@n'(S&,GjPZdr
Haef>*0P'7RmGXkYM.$i
(ok;)'B0#JHZ3OSx>M.z
Od-'kR1X!I(y5iHK7qzf
tTjM)0-P8.oNkhFU%W;Y
iP>efv-F,(O@:

vF56b9?*2l,LfGDQYhU@
!aO6cZdiE"3>j0D@RqCN
AWq@%>"DxE;?RtlCksTV
O-cIY2li<.o7*gXpMR)y
KfX')1rLCBpmoh-ZEw,=
z6f07F35:?JhPI+2S/4O
.XmxE:A*(bjg)1#plt8>
6zS-AanO<htp=@8i5!XG
kB):zSNJM<C$mO9cG@jo
d:GlW*N@cSsuaH%4ZJiB
)Zt'm(fAERsSi&BH/=pc
RQ3H57jeJ!LEK,>1cNDx
Iyd4#%BJxGu'0HsemAKw
w)z1!RBcG6Pf8#<%ULk*
j5+Pyv)r,E>XLoHu?CG.
yl-8&Kr2(JIbFq17Y!/g
o0:r'*7VIOtM95S!@aA,
"uP'N=UmzLaYGHif*,py
U9,3khgMyp'Fa"nb>c0P
-k+G'1DSR2q:Lr(p4Bh3
ur"?G@1FQ*pLTjXPiM-A
>Y&lTi*;QNjVB6u'WZD-
i/HR9j+):3*ET6(7WUVw
5fuomPK%CkcpiUt9T&a+
?).g<%Tw0E4PQH=Bk+xV
4zL<oNef'Dv?5Xy7O$ES
WR0%8Fx4:6LOg5lJ+bhP
M,Jhv&qO>Ies@URp5%Y*
BKehg-rxnSWovHRt3(k;
HFJT7c:g.d=BPk&w9mrI
GatWK=JT+hHN8?*EFy)C
;8TM+d9p5:CUuI%HPsi.
V8P(=w;YLD.yq$:dJ3b4
>o6SC+yHqDJ?!3jIa9h7
XOZo6@5.LEM94kR/7csd
s>R!LH@xFfeg*l;w"DhJ
1jbTOwK;h-=rVaY"zRkQ
PQb6xv3*k.F?JGWo04I,
:Dpz@v=al<s-b&E"fW'n
)Ot-TJ!h/LK9MzVX0Gas
%eE!b4kwz?,'+y"rdNg9
<OAQ.x:gz"nF2!y6N=Wj
A25+<#$=j80cLeK%wB@'
Kh'A5B7R;pidr=(*gT)E
Hp)A5;T"VQjGuO?Z4lf<
20;zlxpDTjhy)>GwsCt(
UO4D><BzwZQY'G/dNaPg
8;D-%ZG(uin7j

y,&ai+Oh8c/LnGv:XJS1
tRxFq'?MvZX6Q*@c>fGE
.BQ?)%oYx&2Zq3VeDIJp
hbVuf;S%'L8s@=!&7<"T
1rbDfC"Mk64%+.$gW79o
7yJ3?!$%t8Tgm;S95:XD
Qwge.Eymx!lXC7%Ib2Dn
3Lu,ax>4Y(KNC%=zX$I?
"Y.ou2wJtr%@3-5<6>*B
V>!TQjK'zUAZP)Rk?Ey;
zeR&hTQ+<3FxPZ0VS8Jr
dkT,:)cglL-Q&xpXt=mu
;z@/*OKs)4jnyuAwag!t
V3g="psKfdxm0wH7FNI?
uWVpxt7r13,S9lGwqD)*
H(a"IYbk8F6WXfwDzSlN
A.GCFPBL&Jwc6Z'Uli1"
:d@AtY)/Gz+f2'(QBV&a
emRC8wSa1EpH'2x"*&3,
AldO-E.?TNcx"=j$4p>1
kYdhRtX?e*C>!AEvWZ"G
<D1zo"+2N7qBUjW!vn3?
yxTKq-HfUmI.N1pkjs:+
6E%VNI;7CT$Dgc3BFA8P
JVIHMq!P;mk>yb%1X9a8
,shxMu5bod2wf-#H?vRy
3CfglMWZi5*jD(!+XwUT
$=oD79:Bz6pt?XgKd1k2
V#;)@ku7vnS8cDPedyB+
0tJm,w;Cqzc"4U!TPpl$
P8m)w:O34po2=$nEs(C%
ZXTuoG/kcUw>"Dvq<6r0
Jci$'vYrAh4waCtQD>-"
8wSozXG=s)6V#a-pQexT
f0w<e*.xaBCpF9U/EJu!
'jOi!JM2U=vYTuLpn<mt
/b3m;U'c!9@aF"&l<wN7
7,ZOUuPC/j(BW8<Kgbtn
vbK@lY4rOP.7Q<&ohUT!
<#1U=lw)>FO!Ga:-Ez(q
zV*$Xh"LKakjt.<2PvDY
*uSYb(RgE6a<pZ&0UHFs
h8CVw$SYd+9)0OUB#-nq
P@j+&(r"b!YRtw,W:s%C
f2/hx=HmwinzV#*9L4Tj
7"YRmFhk$D=M4vN>uoSn
sMrD9l#t!EgvkcT:)X>A
3uPesWSEc/+.t

+r"Xj<ZM;Kl*qYdyF&L.
kVI"3)YGUZ#vL!TJ6H:A
f5BD.dP/t2e+y>"<!GQM
D>.#+(xM;O@EN9jRB6&Y
pf#YtAJk4XbFSduGD@+K
3zN/Z$jCtBi?s6&:AmlX
m-UC#Z8ROA5SFQ<+ejw:
@aOgLVFpxZ>y&5)+k%0:
yJ)>2vw.FaGrm5!b@?T#
wpH.f2RLAk&nWi"6zUTY
f+m>U;Y6vD3"7V2cLH=1
$#hI4z;3ReNWx"oy(<Kk
2ZmQAoC,3Kl=j%H7$v9G
&s3:0X764p$OrH,/ygNz
q0"j)TgK;&?Um'z%a-(w
yvF).xe%J0SPwNM5rRDt
-t2NHsu6eO3C)WYIxw>P
;lOaDKhQ7=4dL>v%WjiG
%57r9l(V2<SfGvt$@>Ok
w(U=Gf-v:+1ycKa>09*)
g53?s"xb4G0z%+V=>TnU
YB'w6g?=5cEdFSIrMbPq
QeNDwhP"4(gKqSmBrY52
0U&%@bji64:c;pz?ey)q
,.<L-+UZ1'R/ljy"JYma
?dFxbNc@ty%RUDA$)fGs
E=oKR0OWbyfZhVNT#s!L
j;OX3,wfTIL9vuFUPcZ-
Yvq9(3/U$oZ:sjEr*8'c
kYcZUL8$ple*AQC3";yd
V0(rqvF&mCRf<2-yB?nx
F.%Zmr)dn(cTYV1E3M4B
gF4(DIvf;aXc1PK2J=#y
%!;fBiL4*0Zg"7#+k9Y3
qkTcL0DG#+ZxW6!71tn=
V91Ea:8RqcZeMr"lS%/A
ebZ!N/.F,A?Cs"q)MRxi
uxn+kY$9=3Udi@2P7:*C
&3@%eb?Y"o#hDwa8ugkr
Hl3+&#Ev@L2ge%i/jyIJ
fE@'8RLY&.jKH5r/SZ39
01>Dq*g"l6Wm#=BKuQHY
AS3UB,xl@&pO90c<j!In
fa.o>G=<q*kMNw(!%8ZX
EZhT(Cjptas2e1F#J%VB
vT."u8mQo)BrzSV'Zt:N
$E/SUm=3J!j4TX.-dygz
?O(+r9wVQHLP/

a8H&-d*!N$R"<vV#q.OA
pj$F1laH,2M>C.Ks0ze-
&o)1fnPg7(Jv'cUGurVl
HUfL/,S36;d&(kt@'Y+I
=c?x5fug-QrdHh:sLUP(
.VNFm9KO$Tb!0l3I:>ZR
V<W&Hp/SBGRYI9Nw3"2Z
r(+Kf5B"o16&n#xZ%wA*
+SpFucBRmPWNrLhtzi#o
>dt@p#EJaML2ZBjO=VG+
;y6alQD4(ecgIN<qJ*jz
+&HzpE6R!-WP9Asn%f>/
"Ydo0EwG;e+rCJav3&?8
Skg=Gs>!zv:8*i@NV"yB
lVbHSyn+B#5D7ade4;Q2
r+U8!eL)ZEy.=J$GADMV
5B9tpHE?ITZ;RA71wV8:
+aMc.0:Hy7ECNUl3-QZX
tv,74E9w21iX$&=cz<;!
sUQrzE.CxkF+)GtHX>1c
>R8Pyb's!m"#@?E0.Kd3
W8?=DAX#*pIVw@,3qy.9
EKYSq4UQ7Xek%cA$v"n!
k?&*xbmf=M0N>lOC!S-o
Y=RJKs'aEz-Z#Sob4QCO
6QqpNK5+3$RXMZ*kvSEd
4gXbSB;j0TUzq1)L'lOQ
Nk9Fvio*G0)q?7EJ"X!/
dT=zZ!f*?X(j#1sNyM6Y
h%;mK@bD>/QIFf'HXslE
N'$hJiEQF.#9Y(w)OM7n
C2mOtK8pjTH=slboZ'XE
Qe&:XmhZD1(Tzs6=)tML
q+%6wb2T/)SWxNM&.j35
Soc0?-1w.&8E)P,#Cls;
DG<%VdJ8Z,2)?z:Q.bho
BV*X&<d-yPK@YMCuz6Se
M@hk2g?VlAc:<,3jE"KP
0,d/'IoD<J.!cF"=#?@1
QrE0.Xo+B>Dg4m3iRwS1
(NI4TYCz";e<Vij$X3#Z
uV&OGNhZF5vm1ric:(.K
;DkVdPS@6ht%Xw+x)-HT
+PK;"tmBv<0S>IJzx(.G
+xe(qPH-UBQT1MaL8Olj
&<0Hcg#T9m2>+Rj)D"Q7
JQTjXFhH5dZEK)WuaB9x
x(Vm-@.LsRth+

...

:-G<1R9mkK=@HQuLfpND
Uq8fl,#o$e+0Ez1ZswhT
Z-l$?&i5<z=g!wA.JmW3
+DZ:.-V>)z1YBeijlonv
b,:Sy"<2OaLHTA5CnUKE
?5ACir1wf;q>B"8Td6H+
+ZS#@jk(>$%cJq8l=1mz
u(2ZbU!s1-LG#4<v,A3H
-;%$5ciJlv=),exN<Fy#
C1(+tY@Bm$wju8)PQEye
ECMRP4?<TGj)gUS.hkF"
uV3xM-sStZW@!X#&zJr6
SHn2z8;$YdwA=B-6gp.I
*&b31U?>8t#6+jh=PVYp
$WQbzwy*kaJcLOSC<D9d
A;w*h'.7/):iU@M<?-zC
!'TiZ@Embc7S0I9/6P,d
Y"?5!I/HX:dAi+,u3('M
84a5-F$m>,N9R6ZLY2QS
iGM1Hha$XR-dcS%QNUn+
78!SU2J&ANdR@p#kbgF1
'NXp4C>IvD:hm9)/,fj0
6mMZBwIX#=iKjrcV;8ED
2Y"/$!lc8zANa5V:j*tI
!fC4gYAR/NErdPX*hI"D
%CSbY.EiGuT*B8M5qox?
cA&!Q5BNKXw:iZu3y>sq
)sKM?/%a9"E>lf!xYvqg
.Ck9PUiZ37l<2Y-H!/Nj
d.XsQFGTtqNby'wkc#vC
6ZP,A(:cOKFgR<sliWkd
TPY.fc!KwWo9LA1#p>2k
akmFy47G8DM6;fIbc3@)
FPQnM"%!pGe>C5U9</oY
Ys&be:d3hAPu1DU4'y=F
A1lLc8(Fh&#i5Pz;e3y4
Yw1@MgjAUu.oZ4qk$zi;
G"r'N@RDKQL&7$mdUHIs
b!L:?O%ay/Z-4n@>zeC'
*ej=3pr6'IYd%nJG7cE$
hOv6u/"DZBdSAPIGlW?w
0?Ysgrn6p32btlRB&K"x
6m*Bg4OzjilApn$S"ubD
t<$Grd8"o3Czu0fXLKi&
>MHXb7tmOGpw+8=euYF$
U?Mv:(#z@n0>oT+,-%/6
Ivyc#irYOk=qEp6l7RQ-
@i2XaPpDShzMn

:OGX1=9"EW03<F4za7S8
;Y5B"raVZkKHShpg=jF/
A5y?vXQEw3o0>a(2B')*
p1+X)q%,Pa'vUT#2cMD6
L(am8nW#27XzVlf@T/u=
Mr0A+Zo?aD@85)UbKe*"
Q*vI5W,(Pz?/jckalrx!
DGoCs5M:B3Vg/UY*(ujw
<H7=5-)AhwB@MJx#>QXl
>PnA,XB7+b;gWGC$wN1i
"4hS'Ya8ZQH?@AJ0NGzm
9q#8&WxTLBy@hDCiStc*
DIt/Y9xwiUb7dqXcEoV4
@OY?78dIE)e"x>%oq$k:
"SX?5)=vQt.W,L6E(VAu
tTI1up#UKf?sm/lX)8vF
52/%cG4-zl0:Ur(+Z*'7
I?bC,(K!UPqST8#nLWwv
%c=YmhMz<jGwL+yH2>:K
?iyfNW/Y!bJ,sjZ"n%hM
XW=*B2lt#UH"1io4gexd
L*syfW)zo=g2U$,mB"0#
&,eIy2nYb-ihlGzDWMZ9
w#U@2EV$(x'1D7Q)gPA;
4>AEc(=e@zrx'8o*blWF
.H"/O*oT+m'2sx@vdKg-
gn#Fr>?SE+yzd-H<hs%W
w+W>yZP=V7M#56irO$23
Xv1>z+ERJNn.aYVeT3:k
QG$r-=fTsBI!blnj7:Nh
u01COj/TJqRS4@B?#tak
DVa*#)+<iRCc!doZ.b08
ALO&+>C(Fi8;d$aJ)s6y
*/L@s+5QJycX-Be,4A>;
xptT%9cUNQk0?X-M!q5S
O>f,NUBuE9kmh;6cjsy'
@b,.vBaf(#%POZ<to'YN
&Qi0Y/?5j*n+HB2pcPxf
a@tR)!6,$LoShGTQ2Y1b
0XZ6wQT@M(DqLo:#<cCU
e.21nP'mjZWfSU;0ct"i
e%XI?,aZ4@NGTwOR$bHx
:P.NCtzv)r;RgMc'=L9Y
83rT5J7wR%pj6D!Q@SN<
hsd+KLOCVU'8.Y"3#ZD-
KJX=:dZaT?*/M"g&F$#V
;5w<Cd$96t2Q"v4zqay#
C3=7F?l@54,Nq

?#3CEz+.rV2/5gUW0vf1
;g/3pU0PK":jsDFu54$z
IeNb?.1ZY0O9+nAEd-W&
oFW<5gMX/!)cPUKNBmYn
hm%l)8GMS1LP:TxA!quK
,9N<vn?h2QVt.G&J7W60
8EPN(nVT$64,YwQFBl;y
0b&X#i/aVd%)?4;3*RvF
U:0QbePh(+SsDM)l.*,C
'D"@I2UQ0el47u1b9x&.
7ES04)OAW'1<dTa&r$2b
1P+5,i/GTraz>fh36n0&
LP)!CVM+(Ri/N?b*Jj%;
7sLb.M02dPfOJIhvCu89
%4m:s)j3c6L+<,YJOM9f
PGjtUKX/zdBlq>eiL1AZ
$cRH!.KN?=%IlSkjQt<V
ZJw/:iC@W*F4<8G(9nPT
Q+oBPAh>K"T1WGXutnLV
zg3Xle1oRwV#/IHJpSmZ
OaUW"?we%9+2(;r.zu>1
T)dYy:WrBJvVF3'GuO6?
a#"5W$m8.FEzNMIjd-:&
Z(<HAr;D61+5NR7t.M&U
;gb&,laWin-yNJD+*UdV
wW=rsUqA#3IYp9?@FRa*
pAa&Fdf5z/Ue8"XB6=-V
81(%f/BDTUhKoJH;G0N3
+!rd6PD#uj;=1/,wm$(*
*o(l3Cw1Hzm'2e#n!BIS
Hj0Rs)DL.b-g:A(kS8Q1
Gln!y4k/'9oT?0z8pM5w
tuHc1<pre!@d,TDBh=Vq
4#p=?xc@K>H'f1in-I6P
Y24'K0z/1GnVQuNxsM*r
ve(q.EX?P;k)8Rfcg*ZI
46%)>M!yqTm3S:@p.jPf
)Ck?ty=e29OMNIlZ7(*-
i(0L,y?1fa3@E2;/)6xl
09df:ZNVUH/Pc&syp85a
0Qb1RgJwF>M37e2)YDln
*,nI>w;?f0Y!s5xQ)C87
p+h9tOD*WjonQ,Awb;()
/ZKDU5%LjW2I'4$.ewCX
FRf0:/aSGDH&qwhM3EUL
vPkM!$yV9b?J2o5lDcd1
!Dh8PSw5qAle;2=Uvnjx
vU:b7E3Rp!Gm<

&vSrzWsg4I.!YZj+;f6X
SLC/n"Wj,EOBXe&A:iml
MgqekH'w$ltU:)Ei+o2p
h(z!=@g,b&aBiw3x>FA8
M(Ln9RSwPky)E2z*JB58
d+7xS3ozAgOcv/sw!8DI
K>W%at=o?@u3MriNd)Bj
rC5,Z+;DMOwhsn0LtQm#
<YRC54PEsB*;1Wf%O7mZ
gj"z#T=BnU$Eb?8oYR:-
;Eh=rKaC05yYzOedsk!D
tb%?+<-UqRd.f8CAvpzm
i;3cjI2zd/7Hl1ex)A:f
MXow65mt3j,J#CqE:*9.
wKoIXGm@9ZY;#s<rWJ"t
yA%XwkO#=p>&:z.,0@/;
V&Ws".rZ%,@LRb/NQc7;
0AaHNVz%U6#@j.?ytlP*
,LaIqiupUYC&MDgHTs?-
=FQmyrn+ajp;7iGv!"U$
U(;sbj+"d*Q4hfr7uN:?
,CpBEv*9MFDY)wZ/=(hA
Mg5NlZi%,jaAF37':R9r
AdWwx%(c:zXvbfNKm9;0
k;iHVnN3194p$2OjlmP+
e&O1UL-!"?*7xao=,/A(
2JYs4GNyRb9v+EXac:/&
8eTd31ONV+Kf0wjG#qb"
>@R%We?dTALX8M=GOE06
fN-rP.Mq!e7BVdtL%y"G
sc6Nm*1lM2RQj@PJZbwX
3>%HGmuVyWI"R):bL'BZ
v,m)?ao@Sbt4LqDG7$XA
-Oa='qV2&j0*kBNJ/Fbf
epQm&Z/l?WDwb$K51-Ss
a8g=MDfE/;VbI6n4jPrs
gCAwPycE/kfSo"6NzR53
2d$%ZXebqi'v=<JKEyS:
!qa0;9:,X'gKPs-c?zVZ
&M<!KD;,a0vP>e7t'uIl
@nC,sE6"ZozF8A/.3f5%
-XRca4$VxIEBih6F<2Db
sO<Nq#MJy.nW6LR=oz:B
Nu"U?Ls;iE0(z)CQFel>
v*EHqb-&BuzYoiPh20%c
TBPgYK7%@Hc3?WUvjfSm
LPCB:JIEFa1rjunTd!9*
QBnm9(XdkzbV"

q@EJxgk8Azbw%Xh.5nt,
A8.<U0JQrgb7X$Nm4Oe-
#AEkW.@pS6J735NC"bP&
UqMkyuP/w@*vpHI7mgs(
%slTLqVx=B'Q?MKSOd!e
0H,E@KA$dn:3IBum-wyS
vr;K4qnS2Op!uEA6bfNh
h&k.Q6cOC1>vBMHFU?YV
<#.>3er:GxHUm"=@(Z-O
vD+.bPY5hS)stXqG*!Cc
)!iAYj7$#gbKFx,ZeXVp
q#CG8)oD6U9Is.1-yKaH
q:mW<if3D$%2PwyVUr6H
x(>R,Zo"=%nDGkK07eIw
X<-FV@Trn*wC4KP'U&=M
5nm&+b;CY*gcLH-sTO%j
aC<1N,GbfS*qnTd4sH9Y
wvcO?/R%gSGI>y7uPo6i
aIS-!#sv<"Lk;oV6R8*=
6,sd!RNg5/YIfku"Ev&z
yb=N4fj-+'RSsDPO%W6*
Jj@n.v9gG4LD+RaTcwhB
M)%BbV(-kzRrX>Y.y=<e
!uFtD&5ncw(2.VXSC*$o
9gm#bu-N*LrPG<ISz.kH
;EeV9Z<%zpWkRDd/o(8g
glw<iU"mr3uDC'@OJdzk
dhfF<>nptoc=QgM6lYVx
WNxBIXf,+Jk?574Y*6F:
xVQv(kAW#9nR%KCgfN&E
lDIM2L,kcvp-<g9tV.ed
kHYy+BeZ7rzw,@=*d3J>
SbknD4;L9wWPslqa%uyJ
jJ0k;U:?Yc+e8xMsXmbD
gI'<w7n9puP#0vj8ZrTM
n:,>j$z+<pD'uFWN7.Br
cE"hCD%anNjSIg*k2MHi


In [10]:
print('Number of false positive: ', falsPositive)

Number of false positive:  251447
